# Test runtime
### Test with IK checkers

**grasp sample 10**  
solve-mean: 1175.2 ms  
solve-median: 740.8 ms  
success rate: 98.0 %  

**grasp sample 20**  
solve-mean: 1190.6 ms  
solve-median: 778.4 ms  
success rate: 96.5 %  

**grasp sample 30**  
solve-mean: 1323.0 ms  
solve-median: 837.4 ms  
success rate: 99.0 %  

### Test without IK checkers

**grasp sample 10**  
solve-mean: 1998.9 ms  
solve-median: 1241.1 ms  
success rate: 88.0 %  

## set running directory to project source

In [1]:
import os
import numpy as np
import time
os.chdir(os.path.join(os.environ["RNB_PLANNING_DIR"], 'src'))
import matplotlib.pyplot as plt

## 4.1 PlanningScene

##### initialize CombinedRobot and GeometryScene

In [2]:
from pkg.controller.combined_robot import *
from pkg.project_config import *
from pkg.geometry.builder.scene_builder import SceneBuilder

s_builder = SceneBuilder(None)   # create scene builder without detector for virtual scene
crob = CombinedRobot(robots_on_scene=[
    RobotConfig(0, RobotType.indy7gripper, ((0,0,0.01), (0,0,0)), None)]
                     , connection_list=[False])
gscene = s_builder.create_gscene(crob)
gtems = s_builder.add_robot_geometries(color=(0,1,0,0.5), display=True, collision=True)
gscene.show_pose(crob.home_pose)

connection command:
indy0: False
Unable to register with master node [http://localhost:11311]: master may not be running yet. Will keep trying.


Unknown tag "hardwareInterface" in /robot[@name='custom_robots']/transmission[@name='indy0_tran0']/actuator[@name='indy0_motor0']
Unknown tag "hardwareInterface" in /robot[@name='custom_robots']/transmission[@name='indy0_tran1']/actuator[@name='indy0_motor1']
Unknown tag "hardwareInterface" in /robot[@name='custom_robots']/transmission[@name='indy0_tran2']/actuator[@name='indy0_motor2']
Unknown tag "hardwareInterface" in /robot[@name='custom_robots']/transmission[@name='indy0_tran3']/actuator[@name='indy0_motor3']
Unknown tag "hardwareInterface" in /robot[@name='custom_robots']/transmission[@name='indy0_tran4']/actuator[@name='indy0_motor4']
Unknown tag "hardwareInterface" in /robot[@name='custom_robots']/transmission[@name='indy0_tran5']/actuator[@name='indy0_motor5']


Please create a subscriber to the marker
publication OK
published: [0, 0, 0, 0, 0, 0]
Please create a subscriber to the marker


##### add geometries

In [3]:
from pkg.geometry.geometry import *

# add environments (fixed=True for non-movable geometries)
wall = gscene.create_safe(GEOTYPE.BOX, "wall", "base_link", (3,3,0.01), (-0.2,0,0), 
                           rpy=(0,np.pi/2,0), color=(0.8,0.8,0.8,0.5), display=True, fixed=True, collision=True)
floor = gscene.create_safe(GEOTYPE.BOX, "floor", "base_link", (0.72,1.52,0.01), (0.25,0,0), 
                           rpy=(0,0,0), color=(0.8,0.8,0.8,0.5), display=True, fixed=True, collision=True)
wp1 = gscene.create_safe(GEOTYPE.BOX, "wp1", "base_link", (0.1,0.1,0.01), (0.6,-0.3,0),rpy=(0,0,0), 
                         color=(0.8,0.2,0.2,1), display=True, fixed=True, collision=True, parent="floor")
wp2 = gscene.create_safe(GEOTYPE.BOX, "wp2", "base_link", (0.1,0.1,0.01), (0.2,-0.3,0), rpy=(0,0,0), 
                         color=(0.8,0.2,0.2,1), display=True, fixed=True, collision=True, parent="floor")
goal = gscene.create_safe(GEOTYPE.BOX, "goal", "base_link", (0.1,0.1,0.01), (0.3,-0.4,0), 
                          rpy=(0,0,0), color=(0.2,0.2,0.8,1), display=True, fixed=True, collision=True)
 
# add movable (fixed=False for movable geometries)
box1 = gscene.create_safe(GEOTYPE.BOX, "box1", "base_link", (0.05,0.05,0.05), (0.3,0.4,0.031), 
                          rpy=(0,0,0), color=(0.8,0.2,0.2,1), display=True, fixed=False, collision=True)

obstacle = gscene.create_safe(GEOTYPE.BOX, "obstacle", "base_link", (0.05,0.05,0.05), (0.5,0.4,0.031), 
                          rpy=(0,0,0), color=(0.8,0.8,0.2,1), display=True, fixed=False, collision=True)

##### create PlanningScene

In [4]:
from pkg.planning.scene import PlanningScene
pscene = PlanningScene(gscene, combined_robot=crob)

##### create_binder
- Binders (or Actors) are binding points where objects can be attached (or binded)
- Examples are 
  - PlacePlane: plane for object placement
  - Gripper2Tool: 2-finger gripper tool for grasp objects
  - SweepTool: action point to pass waypoints for sweep task

In [5]:
from pkg.planning.constraint.constraint_actor import PlacePlane, Gripper2Tool, SweepFramer

In [6]:
# create PlacePlane on geometry "floor" and "goal"
# when point is not set, the entire upper surface of the geometry becomes valid binding area.
# when point is set, the specific point becomes the only valid binding point.
pscene.create_binder(bname="floor", gname="floor", _type=PlacePlane)
pscene.create_binder(bname="goal", gname="goal", _type=PlacePlane)

In [7]:
# add collision boundary for gripper base
# - set link_name="indy0_tcp" to attach the geometry to end-effector link
# - it can be labeled as fixed=True, as it is "fixed" on the indy0_tcp link
gripper =  gscene.create_safe(GEOTYPE.SPHERE, "grip0", link_name="indy0_tcp", 
                                dims=(0.01,0.01,0.01), center=(0,0,0.14), rpy=(-np.pi/2,0,0), 
                                color=(0.8,0.2,0.2,0.5), display=False, fixed=True, collision=False)

# create Gripper2Tool binder
# Gripper2Tool is a 2-finger gripper, which can rotate along z-direction.
# To align the z-direction with the 2 fingers, rotate by 90 degree along roll axis.
# The gripping point is (0,0,0.11) in local coordinate of "gripper" geometry
pscene.create_binder(bname="grip0", gname="grip0", _type=Gripper2Tool, point=(0,0,0), rpy=(0,0,0))

In [8]:
# Add virtual (no-collision) sweep face. the point is 0.2 m away from the "indy0_tcp" link
# To match the z-direction with the target surface, the geometry is rotated 180 degrees in pitch-axis.
sweep_face =  gscene.create_safe(GEOTYPE.BOX, "sweep_face", link_name="indy0_tcp", 
                                dims=(0.05,0.05,0.001), center=(0,0,0.2), rpy=(0,np.pi,0), 
                                color=(0.2,0.2,0.8,0.1), display=False, fixed=True, collision=False)
                                 
# create SweepTool binder
pscene.create_binder(bname="sweep_face", gname="sweep_face", _type=SweepFramer, point=(0,0,0), rpy=(0,0,0))

##### create_subject
* Subject describes the tasks in the planning scene.
* There are 2 categories in subject:
  1. Object: The object has grip points and placement points for pick&place task
  2. Task: The task is can be any non-physical task. Check SweepLineTask for example
* The subjects can be composed of multiple action points. Examples are:
  1. Grasp2Point: grasping point for 2-finger gripper. 
  2. PlacePoint: The point to place object.
  3. SweepPoint: A waypoint for SweepLineTask.
  * The above 3 action points inherit DirectePoint, for which the orientation is free along z-axis. 
  * If "point" parameter is not set, the entire upper surface is becomes valid action area.

In [9]:
from pkg.planning.constraint.constraint_subject import Grasp2Point, PlacePoint, SweepFrame
from pkg.planning.constraint.constraint_subject import CustomObject, SweepLineTask

In [10]:
## create box object with grasping points along positive & negative y-direction and placement point in the bottom face
box_obj = pscene.create_subject(oname="box1", gname="box1", _type=CustomObject, 
                             action_points_dict = {
                                 "handle1": Grasp2Point("handle1", box1, [0,0,0], [-np.pi/2,0,0]),
                                 "handle2": Grasp2Point("handle2", box1, [0,0,0], [np.pi/2,0,0]),
                                 "bottom": PlacePoint("bottom", box1, [0,0,-0.026], [0,0,0])})

In [11]:
## create box object with grasping points along positive & negative y-direction and placement point in the bottom face
obs_obj = pscene.create_subject(oname="obstacle", gname="obstacle", _type=CustomObject, 
                             action_points_dict = {
                                 "handle1": Grasp2Point("handle1", obstacle, [0,0,0], [-np.pi/2,0,0]),
                                 "handle2": Grasp2Point("handle2", obstacle, [0,0,0], [np.pi/2,0,0]),
                                 "bottom": PlacePoint("bottom", obstacle, [0,0,-0.026], [0,0,0])})

In [12]:
## create sweep task with 2 waypoints
sweep = pscene.create_subject(oname="sweep", gname="floor", _type=SweepLineTask, 
                             action_points_dict = {"wp1": SweepFrame("wp1", wp1, [0,0,0.005], [0,0,0]),
                                                   "wp2": SweepFrame("wp2", wp2, [0,0,0.005], [0,0,0])}
                             )

## Pipeline

In [13]:
from pkg.planning.pipeline import PlanningPipeline
ppline = PlanningPipeline(pscene)

In [14]:
from pkg.ui.ui_broker import *

# start UI
ui_broker = UIBroker.instance()
ui_broker.initialize(ppline, s_builder)
ui_broker.start_server()

ui_broker.set_tables()

Dash is running on http://0.0.0.0:8050/

 * Serving Flask app "pkg.ui.dash_launcher" (lazy loading)


##### initialize_state
* initialize_state(robot_pose) updates robot pose and gets corresponding binding status of current scene.
* state.node of ('floor', 0) means the first subject (object) is placed on the floor and the second subject (sweep) has passed 0 waypoints

In [15]:
initial_state = pscene.initialize_state(crob.home_pose)
print(initial_state.node)

('floor', 'floor', 0)


## import planners

In [16]:

from pkg.planning.motion.moveit.moveit_planner import MoveitPlanner
mplan = MoveitPlanner(pscene)
from pkg.planning.filtering.grasp_filter import GraspChecker
from pkg.planning.filtering.reach_filter import ReachChecker
from pkg.planning.filtering.latticized_filter import LatticedChecker
from pkg.planning.filtering.task_clearance_filter import TaskClearanceChecker

gcheck = GraspChecker(pscene)
rcheck = ReachChecker(pscene)

checkers_all = [rcheck, gcheck]

# tcheck = TaskClearanceChecker(pscene, gcheck)
# checkers_all = [tcheck, rcheck, gcheck]

# lcheck = LatticedChecker(pscene, gcheck)
# checkers_all.append(lcheck)

## Test pybullet

In [17]:
os.chdir(os.path.join(os.environ["RNB_PLANNING_DIR"], 'src/scripts/developing/pddlstream'))

In [18]:
from convert_pscene import *
from plan_rnb import *

#### load pybullet, convert scene

In [19]:
connect_notebook(use_gui=False)
urdf_pybullet_path = copy_meshes(gscene)
robot_body, body_names, movable_bodies = pscene_to_pybullet(pscene, urdf_pybullet_path, tool_name="grip0", name_exclude_list=["indy0"])
print('Objects:', body_names)
saver = WorldSaver()

[Pybullet] Load urdf from /home/rnb/Projects/rnb-planning/src/robots/custom_robots_pybullet.urdf
[WARING] non-object subject not implemented for now
('Objects:', {1L: 'goal', 2L: 'floor', 3L: 'wall', 4L: 'obstacle', 5L: 'box1'})


### Test with IK checkers

In [20]:
gtimer = GlobalTimer.instance()
gtimer.reset(stack=True)

In [21]:
log_wFeas = []
for _ in range(200):
    problem = pddlstream_from_problem_rnb(pscene, robot_body, body_names=body_names, 
                                          movable=movable_bodies, checkers=checkers_all,
                                          tool_name="grip0", tool_link_name="indy0_tcp", mplan=mplan, grasp_sample=10)
    _, _, _, stream_map, init, goal = problem
    print('Init:', init)
    print('Goal:', goal)
    print('Streams:', str_from_object(set(stream_map)))
    with Profiler():
        with LockRenderer(lock=not True):
            with gtimer.block("solve"):
                solution = solve(problem, algorithm='adaptive', unit_costs=False, success_cost=INF, max_time=10)
            saver.restore()
    print_solution(solution)
    plan, cost, evaluations = solution
    log_wFeas.append(cost)

Robot: 0
Movable: [4L, 5L]
Fixed: [1, 2, 3]
body 4 - surface 1
body 4 - surface 2
body 4 - surface 3
body 5 - surface 1
body 5 - surface 2
body 5 - surface 3
('Init:', [('CanMove',), ('Conf', q0), ('AtConf', q0), ('HandEmpty',), ('Graspable', 4L), ('Pose', 4L, p0), ('AtPose', 4L, p0), ('Stackable', 4L, 1), ('Stackable', 4L, 2), ('Supported', 4L, p0, 2), ('Stackable', 4L, 3), ('Graspable', 5L), ('Pose', 5L, p1), ('AtPose', 5L, p1), ('Stackable', 5L, 1), ('Stackable', 5L, 2), ('Supported', 5L, p1, 2), ('Stackable', 5L, 3)])
('Goal:', ('and', ('AtConf', q0), ('On', 4L, 1)))
('Streams:', '{TrajCollision, inverse-kinematics, plan-free-motion, plan-holding-motion, sample-grasp, sample-pose, test-cfree-approach-pose, test-cfree-pose-pose, test-cfree-traj-pose}')
Warning! All actions have no cost. Recommend setting unit_costs=True
Warning! Undeclared predicates: ['conf', 'graspable']
Setting negate=True for stream [test-cfree-traj-pose]
Setting negate=True for stream [test-cfree-approach-pose]

Warning! All actions have no cost. Recommend setting unit_costs=True
Warning! Undeclared predicates: ['conf', 'graspable']
Setting negate=True for stream [test-cfree-pose-pose]
Setting negate=True for stream [test-cfree-traj-pose]
Setting negate=True for stream [test-cfree-approach-pose]
Streams: [sample-pose:('?o', '?r')->('?p',), sample-grasp:('?o',)->('?g',), inverse-kinematics:('?o', '?p', '?g')->('?q', '?t'), plan-free-motion:('?q1', '?q2')->('?t',), plan-holding-motion:('?q1', '?q2', '?o', '?g')->('?t',)]
Functions: []
Negated: [test-cfree-pose-pose:('?o1', '?p1', '?o2', '?p2')->(), test-cfree-approach-pose:('?o1', '?p1', '?g1', '?o2', '?p2')->(), test-cfree-traj-pose:('?t', '?o2', '?p2')->()]
Optimizers: []

Iteration: 1 | Complexity: 0 | Skeletons: 0 | Skeleton Queue: 0 | Disabled: 0 | Evaluations: 18 | Eager Calls: 0 | Cost: inf | Search Time: 0.000 | Sample Time: 0.000 | Total Time: 0.000
Attempt: 1 | Results: 1 | Depth: 0 | Success: False | Time: 0.007
Stream plan (inf, 0, i

iter=inf, outs=0) inverse-kinematics:(4, p11, g5)->[]
iter=inf, outs=0) inverse-kinematics:(4, p13, g5)->[]
iter=inf, outs=0) inverse-kinematics:(4, p12, g5)->[]
iter=3, outs=1) sample-pose:(4, 1)->[(p14)]
iter=inf, outs=0) inverse-kinematics:(4, p14, g5)->[]
iter=inf, outs=0) inverse-kinematics:(4, p14, g4)->[]
iter=3, outs=1) sample-grasp:(4)->[(g6)]
iter=inf, outs=1) inverse-kinematics:(4, p11, g6)->[(q13, c13)]
iter=inf, outs=1) test-cfree-traj-pose:(c13, 5, p10)->[()]
iter=inf, outs=1) inverse-kinematics:(4, p9, g6)->[(q14, c14)]
iter=inf, outs=1) test-cfree-traj-pose:(c14, 4, p9)->[()]
iter=inf, outs=1) test-cfree-traj-pose:(c14, 5, p10)->[()]
iter=inf, outs=1) test-cfree-pose-pose:(4, p11, 5, p10)->[()]
iter=inf, outs=1) test-cfree-approach-pose:(4, p9, g6, 5, p10)->[()]
iter=inf, outs=1) test-cfree-approach-pose:(4, p11, g6, 5, p10)->[()]
iter=inf, outs=1) plan-free-motion:(q13, q11)->[(c15)]
iter=inf, outs=1) plan-free-motion:(q11, q14)->[(c16)]
iter=inf, outs=1) plan-holding-

Streams: [sample-pose:('?o', '?r')->('?p',), sample-grasp:('?o',)->('?g',), inverse-kinematics:('?o', '?p', '?g')->('?q', '?t'), plan-free-motion:('?q1', '?q2')->('?t',), plan-holding-motion:('?q1', '?q2', '?o', '?g')->('?t',)]
Functions: []
Negated: [test-cfree-pose-pose:('?o1', '?p1', '?o2', '?p2')->(), test-cfree-approach-pose:('?o1', '?p1', '?g1', '?o2', '?p2')->(), test-cfree-traj-pose:('?t', '?o2', '?p2')->()]
Optimizers: []

Iteration: 1 | Complexity: 0 | Skeletons: 0 | Skeleton Queue: 0 | Disabled: 0 | Evaluations: 18 | Eager Calls: 0 | Cost: inf | Search Time: 0.000 | Sample Time: 0.000 | Total Time: 0.000
Attempt: 1 | Results: 1 | Depth: 0 | Success: False | Time: 0.008
Stream plan (inf, 0, inf): None
Action plan (inf, inf): None
No plan: increasing complexity from 0 to 1

Iteration: 2 | Complexity: 1 | Skeletons: 0 | Skeleton Queue: 0 | Disabled: 0 | Evaluations: 18 | Eager Calls: 0 | Cost: inf | Search Time: 0.008 | Sample Time: 0.000 | Total Time: 0.008
Attempt: 1 | Result

iter=inf, outs=0) inverse-kinematics:(4, p21, g20)->[]
iter=6, outs=1) sample-grasp:(4)->[(g21)]
iter=inf, outs=1) inverse-kinematics:(4, p21, g21)->[(q22, c28)]
iter=inf, outs=1) test-cfree-traj-pose:(c28, 4, p21)->[()]
iter=inf, outs=1) test-cfree-traj-pose:(c28, 5, p22)->[()]
iter=0, outs=1) sample-pose:(4, 1)->[(p23)]
iter=inf, outs=1) inverse-kinematics:(4, p23, g21)->[(q23, c29)]
iter=inf, outs=1) test-cfree-traj-pose:(c29, 5, p22)->[()]
iter=inf, outs=1) test-cfree-pose-pose:(4, p23, 5, p22)->[()]
iter=inf, outs=1) test-cfree-approach-pose:(4, p21, g21, 5, p22)->[()]
iter=inf, outs=1) test-cfree-approach-pose:(4, p23, g21, 5, p22)->[()]
iter=inf, outs=1) plan-free-motion:(q21, q22)->[(c30)]
iter=inf, outs=1) plan-free-motion:(q23, q21)->[(c31)]
iter=inf, outs=1) plan-holding-motion:(q22, q23, 4, g21)->[(c32)]
Summary: {complexity: 2, cost: 0.000, evaluations: 42, iterations: 3, length: 2, run_time: 0.664, sample_time: 0.390, search_time: 0.274, skeletons: 1, solutions: 1, solved

...

Attempt: 1 | Results: 24 | Depth: 1 | Success: False | Time: 0.115
Attempt: 2 | Results: 61 | Depth: 0 | Success: True | Time: 0.249
Stream plan (13, 13, 0.001): [sample-grasp:(4)->(#g193), inverse-kinematics:(4, p909, #g193)->(#q610, #t35230), test-cfree-traj-pose:(#t35230, 4, p909)->(), test-cfree-traj-pose:(#t35230, 5, p910)->(), sample-pose:(4, 1)->(#p257), inverse-kinematics:(4, #p257, #g193)->(#q611, #t35231), test-cfree-traj-pose:(#t35231, 5, p910)->(), test-cfree-pose-pose:(4, #p257, 5, p910)->(), test-cfree-approach-pose:(4, p909, #g193, 5, p910)->(), test-cfree-approach-pose:(4, #p257, #g193, 5, p910)->(), plan-free-motion:(#q611, q801)->(#t35273), plan-free-motion:(q801, #q610)->(#t35274), plan-holding-motion:(#q610, #q611, 4, #g193)->(#t35272)]
Action plan (5, 0.000): [move_free(q801, #q610, #t35274), pick(4, p909, #g193, #q610, #t35230), move_holding(#q610, #q611, 4, #g193, #t35272), place(4, #p257, #g193, #q611, #t35231), move_free(#q611, q801, #t35273)]
iter=0, outs=1) s

Wrote: statistics/py2/kuka-tamp.pkl
         1140738 function calls (1099286 primitive calls) in 0.850 seconds

   Ordered by: internal time
   List reduced from 1515 to 10 due to restriction <10>

   ncalls  tottime  percall  cumtime  percall filename:lineno(function)
        3    0.155    0.052    0.157    0.052 pkg/planning/motion/moveit/moveit_py.py:156(plan_joint_motion_py)
     1450    0.104    0.000    0.104    0.000 {pybullet.calculateInverseKinematics}
        2    0.039    0.020    0.039    0.020 {posix.read}
     9216    0.036    0.000    0.036    0.000 {pybullet.resetJointState}
    56628    0.030    0.000    0.040    0.000 /usr/lib/python2.7/pickle.py:917(load_int)
   113532    0.027    0.000    0.027    0.000 {method 'read' of 'file' objects}
        2    0.026    0.013    0.105    0.053 /usr/lib/python2.7/pickle.py:851(load)
  28393/1    0.022    0.000    0.054    0.054 /usr/lib/python2.7/pickle.py:269(save)
        2    0.020    0.010    0.020    0.010 {posix.fork}
    

Attempt: 1 | Results: 24 | Depth: 1 | Success: False | Time: 0.096
Attempt: 2 | Results: 61 | Depth: 0 | Success: True | Time: 0.205
Stream plan (13, 13, 0.001): [sample-grasp:(4)->(#g196), inverse-kinematics:(4, p919, #g196)->(#q616, #t35407), test-cfree-traj-pose:(#t35407, 5, p920)->(), sample-pose:(4, 1)->(#p260), inverse-kinematics:(4, #p260, #g196)->(#q617, #t35408), test-cfree-traj-pose:(#t35408, 5, p920)->(), test-cfree-traj-pose:(#t35407, 4, p919)->(), test-cfree-pose-pose:(4, #p260, 5, p920)->(), test-cfree-approach-pose:(4, p919, #g196, 5, p920)->(), test-cfree-approach-pose:(4, #p260, #g196, 5, p920)->(), plan-free-motion:(#q617, q810)->(#t35449), plan-free-motion:(q810, #q616)->(#t35451), plan-holding-motion:(#q616, #q617, 4, #g196)->(#t35450)]
Action plan (5, 0.000): [move_free(q810, #q616, #t35451), pick(4, p919, #g196, #q616, #t35407), move_holding(#q616, #q617, 4, #g196, #t35450), place(4, #p260, #g196, #q617, #t35408), move_free(#q617, q810, #t35449)]
iter=0, outs=1) s

iter=inf, outs=1) plan-free-motion:(q813, q814)->[(c1102)]
iter=inf, outs=1) plan-holding-motion:(q814, q815, 4, g627)->[(c1103)]
Summary: {complexity: 2, cost: 0.000, evaluations: 38, iterations: 3, length: 2, run_time: 0.513, sample_time: 0.282, search_time: 0.231, skeletons: 1, solutions: 1, solved: True, timeout: False}

Total External Statistics
External: sample-pose | n: 3550 | p_success: 0.958 | overhead: 0.001
External: sample-grasp | n: 5033 | p_success: 0.994 | overhead: 0.002
External: inverse-kinematics | n: 16421 | p_success: 0.215 | overhead: 0.043
External: plan-free-motion | n: 3568 | p_success: 0.836 | overhead: 0.173
External: plan-holding-motion | n: 1111 | p_success: 0.981 | overhead: 0.066
External: test-cfree-pose-pose | n: 1951 | p_success: 0.999 | overhead: 0.001
External: test-cfree-approach-pose | n: 3858 | p_success: 1.000 | overhead: 0.001
External: test-cfree-traj-pose | n: 7261 | p_success: 0.902 | overhead: 0.001
Wrote: statistics/py2/kuka-tamp.pkl
      

Attempt: 1 | Results: 1 | Depth: 0 | Success: False | Time: 0.008
Stream plan (inf, 0, inf): None
Action plan (inf, inf): None
No plan: increasing complexity from 0 to 1

Iteration: 2 | Complexity: 1 | Skeletons: 0 | Skeleton Queue: 0 | Disabled: 0 | Evaluations: 18 | Eager Calls: 0 | Cost: inf | Search Time: 0.009 | Sample Time: 0.000 | Total Time: 0.009
Attempt: 1 | Results: 11 | Depth: 0 | Success: False | Time: 0.009
Stream plan (inf, 0, inf): None
Action plan (inf, inf): None
No plan: increasing complexity from 1 to 2

Iteration: 3 | Complexity: 2 | Skeletons: 0 | Skeleton Queue: 0 | Disabled: 0 | Evaluations: 18 | Eager Calls: 0 | Cost: inf | Search Time: 0.018 | Sample Time: 0.000 | Total Time: 0.018
Attempt: 1 | Results: 24 | Depth: 1 | Success: False | Time: 0.090
Attempt: 2 | Results: 61 | Depth: 0 | Success: True | Time: 0.196
Stream plan (13, 13, 0.001): [sample-grasp:(4)->(#g199), inverse-kinematics:(4, p929, #g199)->(#q622, #t35600), test-cfree-traj-pose:(#t35600, 4, p929

In [22]:
print(gtimer)

time_array = np.array(gtimer.timelist_dict["solve"])
success_array = np.array(log_wFeas)<1
print("solve-mean: {} ms".format(np.round(np.mean(time_array[np.where(success_array)[0]]), 1)))
print("solve-median: {} ms".format(np.round(np.median(time_array[np.where(success_array)[0]]), 1)))
print("success rate: {} %".format(np.mean(success_array)*100))

solve: 	243934.7 ms/200 = 1219.7 ms (540.866/10240.163)
sample_grasps_4: 	478.3 ms/200 = 2.4 ms (1.757/6.557)
get_stable_4_1: 	335.3 ms/479 = 0.7 ms (0.323/2.132)
ik_fn: 	67606.9 ms/2103 = 32.1 ms (0.507/760.031)
check_feas: 	5255.3 ms/2103 = 2.5 ms (0.498/721.165)
ReachChecker: 	1303.1 ms/2103 = 0.6 ms (0.182/2.267)
GraspChecker: 	2694.6 ms/1502 = 1.8 ms (0.49/720.258)
get_stable_4_2: 	36.0 ms/52 = 0.7 ms (0.3/1.444)
free_motion_gen: 	21796.9 ms/409 = 53.3 ms (4.672/121.219)
holding_motion_gen: 	10275.5 ms/206 = 49.9 ms (28.683/81.184)
get_stable_4_3: 	0.1 ms/23 = 0.0 ms (0.002/0.015)

solve-mean: 1175.2 ms
solve-median: 740.8 ms
success rate: 98.0 %


In [23]:
gtimer = GlobalTimer.instance()
gtimer.reset(stack=True)

In [24]:
log_wFeas = []
for _ in range(200):
    problem = pddlstream_from_problem_rnb(pscene, robot_body, body_names=body_names, 
                                          movable=movable_bodies, checkers=checkers_all,
                                          tool_name="grip0", tool_link_name="indy0_tcp", mplan=mplan, grasp_sample=20)
    _, _, _, stream_map, init, goal = problem
    print('Init:', init)
    print('Goal:', goal)
    print('Streams:', str_from_object(set(stream_map)))
    with Profiler():
        with LockRenderer(lock=not True):
            with gtimer.block("solve"):
                solution = solve(problem, algorithm='adaptive', unit_costs=False, success_cost=INF, max_time=10)
            saver.restore()
    print_solution(solution)
    plan, cost, evaluations = solution
    log_wFeas.append(cost)

Robot: 0
Movable: [4L, 5L]
Fixed: [1, 2, 3]
body 4 - surface 1
body 4 - surface 2
body 4 - surface 3
body 5 - surface 1
body 5 - surface 2
body 5 - surface 3
('Init:', [('CanMove',), ('Conf', q821), ('AtConf', q821), ('HandEmpty',), ('Graspable', 4L), ('Pose', 4L, p931), ('AtPose', 4L, p931), ('Stackable', 4L, 1), ('Stackable', 4L, 2), ('Supported', 4L, p931, 2), ('Stackable', 4L, 3), ('Graspable', 5L), ('Pose', 5L, p932), ('AtPose', 5L, p932), ('Stackable', 5L, 1), ('Stackable', 5L, 2), ('Supported', 5L, p932, 2), ('Stackable', 5L, 3)])
('Goal:', ('and', ('AtConf', q821), ('On', 4L, 1)))
('Streams:', '{TrajCollision, inverse-kinematics, plan-free-motion, plan-holding-motion, sample-grasp, sample-pose, test-cfree-approach-pose, test-cfree-pose-pose, test-cfree-traj-pose}')
Warning! All actions have no cost. Recommend setting unit_costs=True
Warning! Undeclared predicates: ['conf', 'graspable']
Setting negate=True for stream [test-cfree-approach-pose]
Setting negate=True for stream [tes

Attempt: 2 | Results: 61 | Depth: 0 | Success: True | Time: 0.223
Stream plan (13, 13, 0.001): [sample-grasp:(4)->(#g201), sample-pose:(4, 1)->(#p265), inverse-kinematics:(4, #p265, #g201)->(#q627, #t35759), test-cfree-traj-pose:(#t35759, 5, p936)->(), inverse-kinematics:(4, p935, #g201)->(#q626, #t35758), test-cfree-traj-pose:(#t35758, 4, p935)->(), test-cfree-traj-pose:(#t35758, 5, p936)->(), test-cfree-pose-pose:(4, #p265, 5, p936)->(), test-cfree-approach-pose:(4, p935, #g201, 5, p936)->(), test-cfree-approach-pose:(4, #p265, #g201, 5, p936)->(), plan-free-motion:(q826, #q626)->(#t35801), plan-free-motion:(#q627, q826)->(#t35802), plan-holding-motion:(#q626, #q627, 4, #g201)->(#t35800)]
Action plan (5, 0.000): [move_free(q826, #q626, #t35801), pick(4, p935, #g201, #q626, #t35758), move_holding(#q626, #q627, 4, #g201, #t35800), place(4, #p265, #g201, #q627, #t35759), move_free(#q627, q826, #t35802)]
iter=0, outs=1) sample-grasp:(4)->[(g644)]
iter=0, outs=1) sample-pose:(4, 1)->[(p93

iter=inf, outs=0) inverse-kinematics:(4, p946, g648)->[]
Sampling while complexity <= 3

Iteration: 7 | Complexity: 3 | Skeletons: 3 | Skeleton Queue: 36 | Disabled: 0 | Evaluations: 73 | Eager Calls: 0 | Cost: inf | Search Time: 1.178 | Sample Time: 1.085 | Total Time: 2.263
Attempt: 1 | Results: 54 | Depth: 0 | Success: False | Time: 0.026
Stream plan (inf, 0, inf): None
Action plan (inf, inf): None
No plan: increasing complexity from 3 to 4
Sampling for up to 0.120 seconds
iter=3, outs=1) sample-pose:(4, 2)->[(p947)]
iter=inf, outs=0) inverse-kinematics:(4, p947, g648)->[]
iter=4, outs=1) sample-pose:(4, 2)->[(p948)]
iter=inf, outs=0) inverse-kinematics:(4, p948, g648)->[]
Sampling while complexity <= 4

Iteration: 8 | Complexity: 4 | Skeletons: 3 | Skeleton Queue: 36 | Disabled: 0 | Evaluations: 77 | Eager Calls: 0 | Cost: inf | Search Time: 1.214 | Sample Time: 1.450 | Total Time: 2.664
Attempt: 1 | Results: 68 | Depth: 0 | Success: False | Time: 0.031
Stream plan (inf, 0, inf): N

Streams: [sample-pose:('?o', '?r')->('?p',), sample-grasp:('?o',)->('?g',), inverse-kinematics:('?o', '?p', '?g')->('?q', '?t'), plan-free-motion:('?q1', '?q2')->('?t',), plan-holding-motion:('?q1', '?q2', '?o', '?g')->('?t',)]
Functions: []
Negated: [test-cfree-pose-pose:('?o1', '?p1', '?o2', '?p2')->(), test-cfree-approach-pose:('?o1', '?p1', '?g1', '?o2', '?p2')->(), test-cfree-traj-pose:('?t', '?o2', '?p2')->()]
Optimizers: []

Iteration: 1 | Complexity: 0 | Skeletons: 0 | Skeleton Queue: 0 | Disabled: 0 | Evaluations: 18 | Eager Calls: 0 | Cost: inf | Search Time: 0.000 | Sample Time: 0.000 | Total Time: 0.000
Attempt: 1 | Results: 1 | Depth: 0 | Success: False | Time: 0.017
Stream plan (inf, 0, inf): None
Action plan (inf, inf): None
No plan: increasing complexity from 0 to 1

Iteration: 2 | Complexity: 1 | Skeletons: 0 | Skeleton Queue: 0 | Disabled: 0 | Evaluations: 18 | Eager Calls: 0 | Cost: inf | Search Time: 0.018 | Sample Time: 0.000 | Total Time: 0.018
Attempt: 1 | Result

iter=inf, outs=0) inverse-kinematics:(4, p953, g656)->[]
Sampling while complexity <= 2

Iteration: 4 | Complexity: 2 | Skeletons: 1 | Skeleton Queue: 1 | Disabled: 0 | Evaluations: 20 | Eager Calls: 0 | Cost: inf | Search Time: 0.278 | Sample Time: 0.316 | Total Time: 0.595
Attempt: 1 | Results: 27 | Depth: 0 | Success: False | Time: 0.039
Stream plan (inf, 0, inf): None
Action plan (inf, inf): None
No plan: increasing complexity from 2 to 3
Sampling for up to 0.002 seconds
iter=2, outs=1) sample-grasp:(4)->[(g657)]
iter=inf, outs=0) inverse-kinematics:(4, p953, g657)->[]
Sampling while complexity <= 3

Iteration: 5 | Complexity: 3 | Skeletons: 1 | Skeleton Queue: 1 | Disabled: 0 | Evaluations: 21 | Eager Calls: 0 | Cost: inf | Search Time: 0.319 | Sample Time: 0.346 | Total Time: 0.665
Attempt: 1 | Results: 33 | Depth: 0 | Success: False | Time: 0.017
Stream plan (inf, 0, inf): None
Action plan (inf, inf): None
No plan: increasing complexity from 3 to 4
Sampling for up to -0.010 seco

...

Attempt: 1 | Results: 24 | Depth: 1 | Success: False | Time: 0.116
Attempt: 2 | Results: 61 | Depth: 0 | Success: True | Time: 0.257
Stream plan (13, 13, 0.001): [sample-grasp:(4)->(#g393), inverse-kinematics:(4, p1912, #g393)->(#q1248, #t110357), test-cfree-traj-pose:(#t110357, 5, p1913)->(), sample-pose:(4, 1)->(#p511), inverse-kinematics:(4, #p511, #g393)->(#q1249, #t110358), test-cfree-traj-pose:(#t110358, 5, p1913)->(), test-cfree-traj-pose:(#t110357, 4, p1912)->(), test-cfree-pose-pose:(4, #p511, 5, p1913)->(), test-cfree-approach-pose:(4, p1912, #g393, 5, p1913)->(), test-cfree-approach-pose:(4, #p511, #g393, 5, p1913)->(), plan-free-motion:(q1791, #q1248)->(#t110399), plan-free-motion:(#q1249, q1791)->(#t110400), plan-holding-motion:(#q1248, #q1249, 4, #g393)->(#t110401)]
Action plan (5, 0.000): [move_free(q1791, #q1248, #t110399), pick(4, p1912, #g393, #q1248, #t110357), move_holding(#q1248, #q1249, 4, #g393, #t110401), place(4, #p511, #g393, #q1249, #t110358), move_free(#q124

iter=inf, outs=1) plan-free-motion:(q1796, q1794)->[(c2270)]
iter=inf, outs=1) plan-holding-motion:(q1795, q1796, 4, g1320)->[(c2271)]
Summary: {complexity: 2, cost: 0.000, evaluations: 38, iterations: 3, length: 2, run_time: 0.662, sample_time: 0.383, search_time: 0.279, skeletons: 1, solutions: 1, solved: True, timeout: False}

Total External Statistics
External: sample-pose | n: 4165 | p_success: 0.960 | overhead: 0.001
External: sample-grasp | n: 5728 | p_success: 0.994 | overhead: 0.002
External: inverse-kinematics | n: 19269 | p_success: 0.213 | overhead: 0.041
External: plan-free-motion | n: 3964 | p_success: 0.851 | overhead: 0.161
External: plan-holding-motion | n: 1310 | p_success: 0.984 | overhead: 0.064
External: test-cfree-pose-pose | n: 2155 | p_success: 1.000 | overhead: 0.001
External: test-cfree-approach-pose | n: 4263 | p_success: 1.000 | overhead: 0.001
External: test-cfree-traj-pose | n: 8053 | p_success: 0.911 | overhead: 0.001
Wrote: statistics/py2/kuka-tamp.pkl
 

Attempt: 1 | Results: 24 | Depth: 1 | Success: False | Time: 0.114
Attempt: 2 | Results: 61 | Depth: 0 | Success: True | Time: 0.243
Stream plan (13, 13, 0.001): [sample-grasp:(4)->(#g396), sample-pose:(4, 1)->(#p514), inverse-kinematics:(4, #p514, #g396)->(#q1255, #t110535), test-cfree-traj-pose:(#t110535, 5, p1923)->(), inverse-kinematics:(4, p1922, #g396)->(#q1254, #t110534), test-cfree-traj-pose:(#t110534, 4, p1922)->(), test-cfree-traj-pose:(#t110534, 5, p1923)->(), test-cfree-pose-pose:(4, #p514, 5, p1923)->(), test-cfree-approach-pose:(4, p1922, #g396, 5, p1923)->(), test-cfree-approach-pose:(4, #p514, #g396, 5, p1923)->(), plan-free-motion:(q1800, #q1254)->(#t110576), plan-free-motion:(#q1255, q1800)->(#t110578), plan-holding-motion:(#q1254, #q1255, 4, #g396)->(#t110577)]
Action plan (5, 0.000): [move_free(q1800, #q1254, #t110576), pick(4, p1922, #g396, #q1254, #t110534), move_holding(#q1254, #q1255, 4, #g396, #t110577), place(4, #p514, #g396, #q1255, #t110535), move_free(#q125

iter=inf, outs=1) plan-free-motion:(q1805, q1803)->[(c2284)]
iter=inf, outs=1) plan-free-motion:(q1803, q1804)->[(c2285)]
iter=inf, outs=1) plan-holding-motion:(q1804, q1805, 4, g1329)->[(c2286)]
Summary: {complexity: 2, cost: 0.000, evaluations: 40, iterations: 3, length: 2, run_time: 0.512, sample_time: 0.219, search_time: 0.293, skeletons: 1, solutions: 1, solved: True, timeout: False}

Total External Statistics
External: sample-pose | n: 4169 | p_success: 0.960 | overhead: 0.001
External: sample-grasp | n: 5737 | p_success: 0.994 | overhead: 0.002
External: inverse-kinematics | n: 19282 | p_success: 0.213 | overhead: 0.041
External: plan-free-motion | n: 3970 | p_success: 0.852 | overhead: 0.161
External: plan-holding-motion | n: 1313 | p_success: 0.984 | overhead: 0.064
External: test-cfree-pose-pose | n: 2158 | p_success: 1.000 | overhead: 0.001
External: test-cfree-approach-pose | n: 4269 | p_success: 1.000 | overhead: 0.001
External: test-cfree-traj-pose | n: 8062 | p_success: 

Attempt: 1 | Results: 24 | Depth: 1 | Success: False | Time: 0.137
Attempt: 2 | Results: 61 | Depth: 0 | Success: True | Time: 0.253
Stream plan (13, 13, 0.001): [sample-grasp:(4)->(#g399), inverse-kinematics:(4, p1932, #g399)->(#q1260, #t110711), test-cfree-traj-pose:(#t110711, 4, p1932)->(), sample-pose:(4, 1)->(#p517), inverse-kinematics:(4, #p517, #g399)->(#q1261, #t110712), test-cfree-traj-pose:(#t110712, 5, p1933)->(), test-cfree-traj-pose:(#t110711, 5, p1933)->(), test-cfree-pose-pose:(4, #p517, 5, p1933)->(), test-cfree-approach-pose:(4, p1932, #g399, 5, p1933)->(), test-cfree-approach-pose:(4, #p517, #g399, 5, p1933)->(), plan-free-motion:(#q1261, q1809)->(#t110754), plan-free-motion:(q1809, #q1260)->(#t110755), plan-holding-motion:(#q1260, #q1261, 4, #g399)->(#t110753)]
Action plan (5, 0.000): [move_free(q1809, #q1260, #t110755), pick(4, p1932, #g399, #q1260, #t110711), move_holding(#q1260, #q1261, 4, #g399, #t110753), place(4, #p517, #g399, #q1261, #t110712), move_free(#q126

In [25]:
print(gtimer)

time_array = np.array(gtimer.timelist_dict["solve"])
success_array = np.array(log_wFeas)<1
print("solve-mean: {} ms".format(np.round(np.mean(time_array[np.where(success_array)[0]]), 1)))
print("solve-median: {} ms".format(np.round(np.median(time_array[np.where(success_array)[0]]), 1)))
print("success rate: {} %".format(np.mean(success_array)*100))

solve: 	385760.1 ms/200 = 1928.8 ms (580.194/74872.795)
sample_grasps_4: 	834.1 ms/200 = 4.2 ms (2.958/11.621)
get_stable_4_1: 	354.4 ms/494 = 0.7 ms (0.321/1.82)
ik_fn: 	85036.7 ms/2855 = 29.8 ms (0.48/306.074)
check_feas: 	6048.7 ms/2855 = 2.1 ms (0.473/8.119)
ReachChecker: 	1749.6 ms/2855 = 0.6 ms (0.186/2.03)
GraspChecker: 	2579.0 ms/1939 = 1.3 ms (0.493/6.023)
free_motion_gen: 	21553.2 ms/404 = 53.3 ms (4.368/104.328)
holding_motion_gen: 	10695.4 ms/203 = 52.7 ms (30.54/111.264)
get_stable_4_3: 	0.1 ms/15 = 0.0 ms (0.003/0.016)
get_stable_4_2: 	81.8 ms/113 = 0.7 ms (0.334/2.11)

solve-mean: 1190.6 ms
solve-median: 778.4 ms
success rate: 96.5 %


In [21]:
gtimer = GlobalTimer.instance()
gtimer.reset(stack=True)

In [22]:
log_wFeas = []
for _ in range(200):
    problem = pddlstream_from_problem_rnb(pscene, robot_body, body_names=body_names, 
                                          movable=movable_bodies, checkers=checkers_all,
                                          tool_name="grip0", tool_link_name="indy0_tcp", mplan=mplan, grasp_sample=30)
    _, _, _, stream_map, init, goal = problem
    print('Init:', init)
    print('Goal:', goal)
    print('Streams:', str_from_object(set(stream_map)))
    with Profiler():
        with LockRenderer(lock=not True):
            with gtimer.block("solve"):
                solution = solve(problem, algorithm='adaptive', unit_costs=False, success_cost=INF, max_time=10)
            saver.restore()
    print_solution(solution)
    plan, cost, evaluations = solution
    log_wFeas.append(cost)

Robot: 0
Movable: [4L, 5L]
Fixed: [1, 2, 3]
body 4 - surface 1
body 4 - surface 2
body 4 - surface 3
body 5 - surface 1
body 5 - surface 2
body 5 - surface 3
('Init:', [('CanMove',), ('Conf', q0), ('AtConf', q0), ('HandEmpty',), ('Graspable', 4L), ('Pose', 4L, p0), ('AtPose', 4L, p0), ('Stackable', 4L, 1), ('Stackable', 4L, 2), ('Supported', 4L, p0, 2), ('Stackable', 4L, 3), ('Graspable', 5L), ('Pose', 5L, p1), ('AtPose', 5L, p1), ('Stackable', 5L, 1), ('Stackable', 5L, 2), ('Supported', 5L, p1, 2), ('Stackable', 5L, 3)])
('Goal:', ('and', ('AtConf', q0), ('On', 4L, 1)))
('Streams:', '{TrajCollision, inverse-kinematics, plan-free-motion, plan-holding-motion, sample-grasp, sample-pose, test-cfree-approach-pose, test-cfree-pose-pose, test-cfree-traj-pose}')
Warning! All actions have no cost. Recommend setting unit_costs=True
Warning! Undeclared predicates: ['conf', 'graspable']
Setting negate=True for stream [test-cfree-pose-pose]
Setting negate=True for stream [test-cfree-approach-pose]

Attempt: 1 | Results: 24 | Depth: 1 | Success: False | Time: 0.096
Attempt: 2 | Results: 61 | Depth: 0 | Success: True | Time: 0.196
Stream plan (13, 13, 0.001): [sample-grasp:(4)->(#g1), inverse-kinematics:(4, p6, #g1)->(#q8, #t487), test-cfree-traj-pose:(#t487, 5, p7)->(), sample-pose:(4, 1)->(#p3), inverse-kinematics:(4, #p3, #g1)->(#q9, #t488), test-cfree-traj-pose:(#t488, 5, p7)->(), test-cfree-traj-pose:(#t487, 4, p6)->(), test-cfree-pose-pose:(4, #p3, 5, p7)->(), test-cfree-approach-pose:(4, p6, #g1, 5, p7)->(), test-cfree-approach-pose:(4, #p3, #g1, 5, p7)->(), plan-free-motion:(q7, #q8)->(#t529), plan-free-motion:(#q9, q7)->(#t530), plan-holding-motion:(#q8, #q9, 4, #g1)->(#t531)]
Action plan (5, 0.000): [move_free(q7, #q8, #t529), pick(4, p6, #g1, #q8, #t487), move_holding(#q8, #q9, 4, #g1, #t531), place(4, #p3, #g1, #q9, #t488), move_free(#q9, q7, #t530)]
iter=0, outs=1) sample-grasp:(4)->[(g3)]
iter=inf, outs=0) inverse-kinematics:(4, p6, g3)->[]
Sampling for up to 0.221 se

iter=inf, outs=1) plan-holding-motion:(q11, q12, 4, g8)->[(c15)]
Summary: {complexity: 5, cost: 0.000, evaluations: 41, iterations: 6, length: 2, run_time: 0.730, sample_time: 0.473, search_time: 0.257, skeletons: 1, solutions: 1, solved: True, timeout: False}

Total External Statistics
External: sample-pose | n: 4796 | p_success: 0.961 | overhead: 0.001
External: sample-grasp | n: 6454 | p_success: 0.995 | overhead: 0.002
External: inverse-kinematics | n: 21759 | p_success: 0.214 | overhead: 0.040
External: plan-free-motion | n: 4403 | p_success: 0.863 | overhead: 0.151
External: plan-holding-motion | n: 1526 | p_success: 0.986 | overhead: 0.063
External: test-cfree-pose-pose | n: 2388 | p_success: 1.000 | overhead: 0.001
External: test-cfree-approach-pose | n: 4713 | p_success: 1.000 | overhead: 0.001
External: test-cfree-traj-pose | n: 8840 | p_success: 0.919 | overhead: 0.001
Wrote: statistics/py2/kuka-tamp.pkl
         1493999 function calls (1441874 primitive calls) in 0.958 seco

Streams: [sample-pose:('?o', '?r')->('?p',), sample-grasp:('?o',)->('?g',), inverse-kinematics:('?o', '?p', '?g')->('?q', '?t'), plan-free-motion:('?q1', '?q2')->('?t',), plan-holding-motion:('?q1', '?q2', '?o', '?g')->('?t',)]
Functions: []
Negated: [test-cfree-pose-pose:('?o1', '?p1', '?o2', '?p2')->(), test-cfree-approach-pose:('?o1', '?p1', '?g1', '?o2', '?p2')->(), test-cfree-traj-pose:('?t', '?o2', '?p2')->()]
Optimizers: []

Iteration: 1 | Complexity: 0 | Skeletons: 0 | Skeleton Queue: 0 | Disabled: 0 | Evaluations: 18 | Eager Calls: 0 | Cost: inf | Search Time: 0.000 | Sample Time: 0.000 | Total Time: 0.000
Attempt: 1 | Results: 1 | Depth: 0 | Success: False | Time: 0.007
Stream plan (inf, 0, inf): None
Action plan (inf, inf): None
No plan: increasing complexity from 0 to 1

Iteration: 2 | Complexity: 1 | Skeletons: 0 | Skeleton Queue: 0 | Disabled: 0 | Evaluations: 18 | Eager Calls: 0 | Cost: inf | Search Time: 0.007 | Sample Time: 0.000 | Total Time: 0.007
Attempt: 1 | Result

iter=inf, outs=0) inverse-kinematics:(4, p24, g19)->[]
iter=2, outs=1) sample-pose:(4, 2)->[(p25)]
iter=inf, outs=1) inverse-kinematics:(4, p25, g19)->[(q24, c24)]
iter=inf, outs=1) test-cfree-traj-pose:(c24, 5, p17)->[()]
iter=inf, outs=0) inverse-kinematics:(4, p25, g22)->[]
iter=3, outs=1) sample-pose:(4, 2)->[(p26)]
iter=inf, outs=0) inverse-kinematics:(4, p26, g19)->[]
iter=4, outs=1) sample-pose:(4, 2)->[(p27)]
iter=inf, outs=0) inverse-kinematics:(4, p27, g19)->[]
iter=inf, outs=0) inverse-kinematics:(4, p23, g17)->[]
iter=inf, outs=1) inverse-kinematics:(4, p24, g17)->[(q26, c25)]
Sampling while complexity <= 4

Iteration: 8 | Complexity: 4 | Skeletons: 3 | Skeleton Queue: 28 | Disabled: 0 | Evaluations: 63 | Eager Calls: 0 | Cost: inf | Search Time: 2.088 | Sample Time: 2.073 | Total Time: 4.161
Attempt: 1 | Results: 226 | Depth: 0 | Success: False | Time: 0.088
Stream plan (inf, 0, inf): None
Action plan (inf, inf): None
No plan: increasing complexity from 4 to 5
Sampling for

...

Wrote: statistics/py2/kuka-tamp.pkl
         1385859 function calls (1332513 primitive calls) in 0.846 seconds

   Ordered by: internal time
   List reduced from 1515 to 10 due to restriction <10>

   ncalls  tottime  percall  cumtime  percall filename:lineno(function)
        3    0.114    0.038    0.114    0.038 pkg/planning/motion/moveit/moveit_py.py:156(plan_joint_motion_py)
      718    0.060    0.000    0.060    0.000 {pybullet.calculateInverseKinematics}
    79992    0.058    0.000    0.074    0.000 /usr/lib/python2.7/pickle.py:917(load_int)
        2    0.049    0.025    0.189    0.094 /usr/lib/python2.7/pickle.py:851(load)
        2    0.036    0.018    0.036    0.018 {posix.read}
   160260    0.034    0.000    0.034    0.000 {method 'read' of 'file' objects}
    79960    0.028    0.000    0.040    0.000 /usr/lib/python2.7/pickle.py:1184(load_append)
  40076/1    0.028    0.000    0.068    0.068 /usr/lib/python2.7/pickle.py:269(save)
        2    0.021    0.011    0.021    0.0

Attempt: 1 | Results: 24 | Depth: 1 | Success: False | Time: 0.091
Attempt: 2 | Results: 61 | Depth: 0 | Success: True | Time: 0.247
Stream plan (13, 13, 0.001): [sample-grasp:(4)->(#g197), sample-pose:(4, 1)->(#p257), inverse-kinematics:(4, #p257, #g197)->(#q619, #t44414), test-cfree-traj-pose:(#t44414, 5, p955)->(), inverse-kinematics:(4, p954, #g197)->(#q618, #t44413), test-cfree-traj-pose:(#t44413, 4, p954)->(), test-cfree-traj-pose:(#t44413, 5, p955)->(), test-cfree-pose-pose:(4, #p257, 5, p955)->(), test-cfree-approach-pose:(4, p954, #g197, 5, p955)->(), test-cfree-approach-pose:(4, #p257, #g197, 5, p955)->(), plan-free-motion:(q896, #q618)->(#t44455), plan-free-motion:(#q619, q896)->(#t44457), plan-holding-motion:(#q618, #q619, 4, #g197)->(#t44456)]
Action plan (5, 0.000): [move_free(q896, #q618, #t44455), pick(4, p954, #g197, #q618, #t44413), move_holding(#q618, #q619, 4, #g197, #t44456), place(4, #p257, #g197, #q619, #t44414), move_free(#q619, q896, #t44457)]
iter=0, outs=1) s

iter=inf, outs=0) inverse-kinematics:(4, p962, g734)->[]
iter=inf, outs=0) inverse-kinematics:(4, p958, g734)->[]
iter=inf, outs=0) inverse-kinematics:(4, p957, g734)->[]

Iteration: 8 | Complexity: 4 | Skeletons: 3 | Skeleton Queue: 32 | Disabled: 0 | Evaluations: 64 | Eager Calls: 0 | Cost: inf | Search Time: 1.260 | Sample Time: 1.616 | Total Time: 2.876
Attempt: 1 | Results: 300 | Depth: 0 | Success: False | Time: 0.092
Stream plan (inf, 0, inf): None
Action plan (inf, inf): None
No plan: increasing complexity from 4 to 5
Sampling for up to -0.264 seconds
Sampling while complexity <= 5
iter=inf, outs=1) test-cfree-traj-pose:(c1150, 4, p954)->[()]
iter=inf, outs=1) test-cfree-pose-pose:(4, p956, 5, p955)->[()]
iter=inf, outs=1) test-cfree-approach-pose:(4, p954, g734, 5, p955)->[()]
iter=inf, outs=1) test-cfree-approach-pose:(4, p956, g734, 5, p955)->[()]
iter=inf, outs=1) plan-free-motion:(q896, q904)->[(c1152)]
iter=inf, outs=1) plan-free-motion:(q905, q896)->[(c1153)]
iter=inf, o

Streams: [sample-pose:('?o', '?r')->('?p',), sample-grasp:('?o',)->('?g',), inverse-kinematics:('?o', '?p', '?g')->('?q', '?t'), plan-free-motion:('?q1', '?q2')->('?t',), plan-holding-motion:('?q1', '?q2', '?o', '?g')->('?t',)]
Functions: []
Negated: [test-cfree-pose-pose:('?o1', '?p1', '?o2', '?p2')->(), test-cfree-approach-pose:('?o1', '?p1', '?g1', '?o2', '?p2')->(), test-cfree-traj-pose:('?t', '?o2', '?p2')->()]
Optimizers: []

Iteration: 1 | Complexity: 0 | Skeletons: 0 | Skeleton Queue: 0 | Disabled: 0 | Evaluations: 18 | Eager Calls: 0 | Cost: inf | Search Time: 0.000 | Sample Time: 0.000 | Total Time: 0.000
Attempt: 1 | Results: 1 | Depth: 0 | Success: False | Time: 0.008
Stream plan (inf, 0, inf): None
Action plan (inf, inf): None
No plan: increasing complexity from 0 to 1

Iteration: 2 | Complexity: 1 | Skeletons: 0 | Skeleton Queue: 0 | Disabled: 0 | Evaluations: 18 | Eager Calls: 0 | Cost: inf | Search Time: 0.008 | Sample Time: 0.000 | Total Time: 0.008
Attempt: 1 | Result

iter=inf, outs=0) inverse-kinematics:(4, p975, g738)->[]
iter=4, outs=1) sample-grasp:(4)->[(g740)]
iter=inf, outs=1) inverse-kinematics:(4, p972, g740)->[(q925, c1166)]
iter=inf, outs=1) test-cfree-traj-pose:(c1166, 5, p967)->[()]
iter=inf, outs=1) inverse-kinematics:(4, p966, g740)->[(q926, c1167)]
iter=inf, outs=1) test-cfree-traj-pose:(c1167, 4, p966)->[()]
iter=inf, outs=1) test-cfree-traj-pose:(c1167, 5, p967)->[()]
iter=inf, outs=1) test-cfree-traj-pose:(c1161, 4, p972)->[()]
iter=inf, outs=1) test-cfree-pose-pose:(4, p971, 5, p967)->[()]
iter=inf, outs=1) test-cfree-pose-pose:(4, p972, 5, p967)->[()]
iter=inf, outs=1) test-cfree-approach-pose:(4, p971, g738, 5, p967)->[()]
iter=inf, outs=1) test-cfree-approach-pose:(4, p966, g740, 5, p967)->[()]
iter=inf, outs=1) test-cfree-approach-pose:(4, p972, g740, 5, p967)->[()]
iter=inf, outs=1) test-cfree-approach-pose:(4, p972, g738, 5, p967)->[()]
iter=inf, outs=1) plan-free-motion:(q911, q909)->[(c1168)]
iter=inf, outs=1) plan-free-m

In [23]:
print(gtimer)

time_array = np.array(gtimer.timelist_dict["solve"])
success_array = np.array(log_wFeas)<1
print("solve-mean: {} ms".format(np.round(np.mean(time_array[np.where(success_array)[0]]), 1)))
print("solve-median: {} ms".format(np.round(np.median(time_array[np.where(success_array)[0]]), 1)))
print("success rate: {} %".format(np.mean(success_array)*100))

solve: 	283177.6 ms/200 = 1415.9 ms (583.68/10853.301)
sample_grasps_4: 	1193.4 ms/200 = 6.0 ms (4.451/16.835)
ik_fn: 	79404.0 ms/2514 = 31.6 ms (0.466/356.651)
check_feas: 	5203.4 ms/2514 = 2.1 ms (0.458/8.074)
ReachChecker: 	1512.4 ms/2514 = 0.6 ms (0.183/2.167)
GraspChecker: 	2229.5 ms/1738 = 1.3 ms (0.48/4.701)
get_stable_4_1: 	338.1 ms/479 = 0.7 ms (0.347/1.931)
get_stable_4_2: 	68.9 ms/97 = 0.7 ms (0.367/1.564)
free_motion_gen: 	22379.3 ms/426 = 52.5 ms (4.288/110.308)
holding_motion_gen: 	10800.8 ms/210 = 51.4 ms (26.534/98.078)
get_stable_4_3: 	0.1 ms/15 = 0.0 ms (0.002/0.02)

solve-mean: 1323.0 ms
solve-median: 837.4 ms
success rate: 99.0 %


### Test without IK checkers

In [20]:
gtimer = GlobalTimer.instance()
gtimer.reset(stack=True)

In [21]:
log_woFeas = []
for _ in range(100):
    problem = pddlstream_from_problem_rnb(pscene, robot_body, body_names=body_names, 
                                          movable=movable_bodies, checkers=[],
                                          tool_name="grip0", tool_link_name="indy0_tcp", mplan=mplan, grasp_sample=10)
    _, _, _, stream_map, init, goal = problem
    print('Init:', init)
    print('Goal:', goal)
    print('Streams:', str_from_object(set(stream_map)))
    with Profiler():
        with LockRenderer(lock=not True):
            with gtimer.block("solve"):
                solution = solve(problem, algorithm='adaptive', unit_costs=False, success_cost=INF, max_time=10)
            saver.restore()
    print_solution(solution)
    plan, cost, evaluations = solution
    log_woFeas.append(cost)

Robot: 0
Movable: [4L, 5L]
Fixed: [1, 2, 3]
body 4 - surface 1
body 4 - surface 2
body 4 - surface 3
body 5 - surface 1
body 5 - surface 2
body 5 - surface 3
('Init:', [('CanMove',), ('Conf', q0), ('AtConf', q0), ('HandEmpty',), ('Graspable', 4L), ('Pose', 4L, p0), ('AtPose', 4L, p0), ('Stackable', 4L, 1), ('Stackable', 4L, 2), ('Supported', 4L, p0, 2), ('Stackable', 4L, 3), ('Graspable', 5L), ('Pose', 5L, p1), ('AtPose', 5L, p1), ('Stackable', 5L, 1), ('Stackable', 5L, 2), ('Supported', 5L, p1, 2), ('Stackable', 5L, 3)])
('Goal:', ('and', ('AtConf', q0), ('On', 4L, 1)))
('Streams:', '{TrajCollision, inverse-kinematics, plan-free-motion, plan-holding-motion, sample-grasp, sample-pose, test-cfree-approach-pose, test-cfree-pose-pose, test-cfree-traj-pose}')
Warning! All actions have no cost. Recommend setting unit_costs=True
Warning! Undeclared predicates: ['conf', 'graspable']
Setting negate=True for stream [test-cfree-approach-pose]
Setting negate=True for stream [test-cfree-traj-pose]

Attempt: 1 | Results: 24 | Depth: 1 | Success: False | Time: 0.084
Attempt: 2 | Results: 61 | Depth: 0 | Success: True | Time: 0.187
Stream plan (13, 13, 0.001): [sample-grasp:(4)->(#g1), sample-pose:(4, 1)->(#p1), inverse-kinematics:(4, #p1, #g1)->(#q3, #t74), test-cfree-traj-pose:(#t74, 5, p5)->(), inverse-kinematics:(4, p4, #g1)->(#q2, #t73), test-cfree-traj-pose:(#t73, 5, p5)->(), test-cfree-traj-pose:(#t73, 4, p4)->(), test-cfree-pose-pose:(4, #p1, 5, p5)->(), test-cfree-approach-pose:(4, p4, #g1, 5, p5)->(), test-cfree-approach-pose:(4, #p1, #g1, 5, p5)->(), plan-free-motion:(#q3, q3)->(#t116), plan-free-motion:(q3, #q2)->(#t117), plan-holding-motion:(#q2, #q3, 4, #g1)->(#t115)]
Action plan (5, 0.000): [move_free(q3, #q2, #t117), pick(4, p4, #g1, #q2, #t73), move_holding(#q2, #q3, 4, #g1, #t115), place(4, #p1, #g1, #q3, #t74), move_free(#q3, q3, #t116)]
iter=0, outs=1) sample-grasp:(4)->[(g1)]
iter=0, outs=1) sample-pose:(4, 1)->[(p6)]
iter=inf, outs=0) inverse-kinematics:(4, p6,

iter=inf, outs=0) inverse-kinematics:(4, p11, g3)->[]
iter=1, outs=1) sample-grasp:(4)->[(g4)]
iter=inf, outs=1) inverse-kinematics:(4, p10, g4)->[(q7, c10)]
iter=inf, outs=1) test-cfree-traj-pose:(c10, 5, p9)->[()]
iter=inf, outs=0) inverse-kinematics:(4, p8, g4)->[]
iter=inf, outs=1) inverse-kinematics:(4, p11, g4)->[(q8, c11)]
iter=inf, outs=1) test-cfree-traj-pose:(c11, 5, p9)->[()]

Iteration: 5 | Complexity: 3 | Skeletons: 1 | Skeleton Queue: 3 | Disabled: 0 | Evaluations: 32 | Eager Calls: 0 | Cost: inf | Search Time: 0.226 | Sample Time: 0.602 | Total Time: 0.828
Attempt: 1 | Results: 75 | Depth: 1 | Success: False | Time: 0.208
Attempt: 2 | Results: 209 | Depth: 1 | Success: False | Time: 0.400
Attempt: 3 | Results: 337 | Depth: 0 | Success: True | Time: 0.685
Stream plan (25, 20, 0.001): [sample-grasp:(4)->(g4), sample-pose:(4, 1)->(p10), inverse-kinematics:(4, p10, g4)->(q7, c10), test-cfree-traj-pose:(c10, 5, p9)->(), sample-grasp:(4)->(g3), inverse-kinematics:(4, p8, g3)->

Streams: [sample-pose:('?o', '?r')->('?p',), sample-grasp:('?o',)->('?g',), inverse-kinematics:('?o', '?p', '?g')->('?q', '?t'), plan-free-motion:('?q1', '?q2')->('?t',), plan-holding-motion:('?q1', '?q2', '?o', '?g')->('?t',)]
Functions: []
Negated: [test-cfree-pose-pose:('?o1', '?p1', '?o2', '?p2')->(), test-cfree-approach-pose:('?o1', '?p1', '?g1', '?o2', '?p2')->(), test-cfree-traj-pose:('?t', '?o2', '?p2')->()]
Optimizers: []

Iteration: 1 | Complexity: 0 | Skeletons: 0 | Skeleton Queue: 0 | Disabled: 0 | Evaluations: 18 | Eager Calls: 0 | Cost: inf | Search Time: 0.000 | Sample Time: 0.000 | Total Time: 0.000
Attempt: 1 | Results: 1 | Depth: 0 | Success: False | Time: 0.007
Stream plan (inf, 0, inf): None
Action plan (inf, inf): None
No plan: increasing complexity from 0 to 1

Iteration: 2 | Complexity: 1 | Skeletons: 0 | Skeleton Queue: 0 | Disabled: 0 | Evaluations: 18 | Eager Calls: 0 | Cost: inf | Search Time: 0.007 | Sample Time: 0.000 | Total Time: 0.007
Attempt: 1 | Result

iter=inf, outs=0) inverse-kinematics:(4, p25, g14)->[]
iter=5, outs=1) sample-grasp:(4)->[(g16)]
iter=inf, outs=0) inverse-kinematics:(4, p20, g16)->[]
iter=inf, outs=0) inverse-kinematics:(4, p21, g16)->[]
iter=inf, outs=0) inverse-kinematics:(4, p22, g16)->[]
iter=inf, outs=0) inverse-kinematics:(4, p23, g16)->[]
iter=inf, outs=0) inverse-kinematics:(4, p24, g16)->[]
iter=inf, outs=0) inverse-kinematics:(4, p25, g16)->[]

Iteration: 9 | Complexity: 6 | Skeletons: 2 | Skeleton Queue: 13 | Disabled: 0 | Evaluations: 40 | Eager Calls: 0 | Cost: inf | Search Time: 3.827 | Sample Time: 5.835 | Total Time: 9.662
Attempt: 1 | Results: 816 | Depth: 0 | Success: True | Time: 0.573
Stream plan (25, 20, 0.001): [sample-grasp:(4)->(g11), inverse-kinematics:(4, p18, g11)->(#q15, #t953), sample-pose:(4, 2)->(#p7), inverse-kinematics:(4, #p7, g11)->(#q23, #t2097), sample-pose:(4, 1)->(p21), sample-grasp:(4)->(g15), inverse-kinematics:(4, p21, g15)->(q12, c14), inverse-kinematics:(4, #p7, g15)->(#q1

...

Attempt: 1 | Results: 24 | Depth: 1 | Success: False | Time: 0.091
Attempt: 2 | Results: 61 | Depth: 0 | Success: True | Time: 0.204
Stream plan (13, 13, 0.001): [sample-grasp:(4)->(#g96), sample-pose:(4, 1)->(#p148), inverse-kinematics:(4, #p148, #g96)->(#q389, #t27462), test-cfree-traj-pose:(#t27462, 5, p502)->(), inverse-kinematics:(4, p501, #g96)->(#q388, #t27461), test-cfree-traj-pose:(#t27461, 4, p501)->(), test-cfree-traj-pose:(#t27461, 5, p502)->(), test-cfree-pose-pose:(4, #p148, 5, p502)->(), test-cfree-approach-pose:(4, p501, #g96, 5, p502)->(), test-cfree-approach-pose:(4, #p148, #g96, 5, p502)->(), plan-free-motion:(q416, #q388)->(#t27503), plan-free-motion:(#q389, q416)->(#t27505), plan-holding-motion:(#q388, #q389, 4, #g96)->(#t27504)]
Action plan (5, 0.000): [move_free(q416, #q388, #t27503), pick(4, p501, #g96, #q388, #t27461), move_holding(#q388, #q389, 4, #g96, #t27504), place(4, #p148, #g96, #q389, #t27462), move_free(#q389, q416, #t27505)]
iter=0, outs=1) sample-gra

Attempt: 1 | Results: 24 | Depth: 1 | Success: False | Time: 0.088
Attempt: 2 | Results: 61 | Depth: 0 | Success: True | Time: 0.174
Stream plan (13, 13, 0.001): [sample-grasp:(4)->(#g97), inverse-kinematics:(4, p507, #g97)->(#q396, #t27934), test-cfree-traj-pose:(#t27934, 4, p507)->(), sample-pose:(4, 1)->(#p151), inverse-kinematics:(4, #p151, #g97)->(#q397, #t27935), test-cfree-traj-pose:(#t27935, 5, p508)->(), test-cfree-traj-pose:(#t27934, 5, p508)->(), test-cfree-pose-pose:(4, #p151, 5, p508)->(), test-cfree-approach-pose:(4, p507, #g97, 5, p508)->(), test-cfree-approach-pose:(4, #p151, #g97, 5, p508)->(), plan-free-motion:(#q397, q425)->(#t27976), plan-free-motion:(q425, #q396)->(#t27977), plan-holding-motion:(#q396, #q397, 4, #g97)->(#t27978)]
Action plan (5, 0.000): [move_free(q425, #q396, #t27977), pick(4, p507, #g97, #q396, #t27934), move_holding(#q396, #q397, 4, #g97, #t27978), place(4, #p151, #g97, #q397, #t27935), move_free(#q397, q425, #t27976)]
iter=0, outs=1) sample-gra

iter=inf, outs=0) inverse-kinematics:(4, p515, g324)->[]
iter=1, outs=1) sample-grasp:(4)->[(g325)]
iter=inf, outs=0) inverse-kinematics:(4, p514, g325)->[]
iter=inf, outs=0) inverse-kinematics:(4, p515, g325)->[]

Iteration: 5 | Complexity: 3 | Skeletons: 1 | Skeleton Queue: 3 | Disabled: 0 | Evaluations: 24 | Eager Calls: 0 | Cost: inf | Search Time: 0.242 | Sample Time: 1.083 | Total Time: 1.326
Attempt: 1 | Results: 28 | Depth: 0 | Success: False | Time: 0.018
Stream plan (inf, 0, inf): None
Action plan (inf, inf): None
No plan: increasing complexity from 3 to 4
Sampling for up to -0.823 seconds
Sampling while complexity <= 4
iter=2, outs=1) sample-pose:(4, 1)->[(p516)]
iter=inf, outs=0) inverse-kinematics:(4, p516, g324)->[]
iter=inf, outs=0) inverse-kinematics:(4, p516, g325)->[]
iter=2, outs=1) sample-grasp:(4)->[(g326)]
iter=inf, outs=0) inverse-kinematics:(4, p514, g326)->[]
iter=inf, outs=0) inverse-kinematics:(4, p516, g326)->[]
iter=inf, outs=0) inverse-kinematics:(4, p515,

iter=inf, outs=0) inverse-kinematics:(4, p521, g324)->[]
iter=inf, outs=0) inverse-kinematics:(4, p521, g326)->[]
iter=inf, outs=0) inverse-kinematics:(4, p521, g328)->[]
iter=inf, outs=0) inverse-kinematics:(4, p521, g325)->[]
iter=3, outs=1) sample-pose:(4, 2)->[(p522)]
iter=inf, outs=1) inverse-kinematics:(4, p522, g327)->[(q439, c530)]
iter=inf, outs=1) test-cfree-traj-pose:(c530, 5, p513)->[()]
iter=inf, outs=0) inverse-kinematics:(4, p522, g324)->[]
iter=inf, outs=0) inverse-kinematics:(4, p522, g325)->[]
iter=inf, outs=0) inverse-kinematics:(4, p522, g328)->[]
iter=inf, outs=0) inverse-kinematics:(4, p522, g326)->[]

Iteration: 9 | Complexity: 5 | Skeletons: 3 | Skeleton Queue: 25 | Disabled: 0 | Evaluations: 79 | Eager Calls: 0 | Cost: inf | Search Time: 3.376 | Sample Time: 6.289 | Total Time: 9.666
Attempt: 1 | Results: 710 | Depth: 0 | Success: False | Time: 0.221
Stream plan (inf, 0, inf): None
Action plan (inf, inf): None
No plan: increasing complexity from 5 to 6
Sampling

iter=inf, outs=1) plan-free-motion:(q444, q445)->[(c534)]
iter=inf, outs=1) plan-free-motion:(q446, q444)->[(c535)]
iter=inf, outs=1) plan-holding-motion:(q445, q446, 4, g334)->[(c536)]
Summary: {complexity: 7, cost: 0.000, evaluations: 41, iterations: 8, length: 2, run_time: 1.434, sample_time: 1.106, search_time: 0.328, skeletons: 1, solutions: 1, solved: True, timeout: False}

Total External Statistics
External: sample-pose | n: 6108 | p_success: 0.961 | overhead: 0.001
External: sample-grasp | n: 8011 | p_success: 0.995 | overhead: 0.002
External: inverse-kinematics | n: 26835 | p_success: 0.218 | overhead: 0.047
External: plan-free-motion | n: 5315 | p_success: 0.882 | overhead: 0.134
External: plan-holding-motion | n: 1977 | p_success: 0.989 | overhead: 0.060
External: test-cfree-pose-pose | n: 2863 | p_success: 1.000 | overhead: 0.001
External: test-cfree-approach-pose | n: 5642 | p_success: 1.000 | overhead: 0.001
External: test-cfree-traj-pose | n: 10545 | p_success: 0.932 | o

In [22]:
print(gtimer)

time_array = np.array(gtimer.timelist_dict["solve"])
success_array = np.array(log_woFeas)<1
print("solve-mean: {} ms".format(np.round(np.mean(time_array[np.where(success_array)[0]]), 1)))
print("solve-median: {} ms".format(np.round(np.median(time_array[np.where(success_array)[0]]), 1)))
print("success rate: {} %".format(np.mean(success_array)*100))

solve: 	293849.8 ms/100 = 2938.5 ms (655.159/10540.996)
sample_grasps_4: 	244.9 ms/100 = 2.4 ms (1.551/6.342)
ik_fn: 	166923.9 ms/1325 = 126.0 ms (4.544/349.284)
check_feas: 	837.8 ms/1325 = 0.6 ms (0.283/2.082)
get_stable_4_1: 	212.9 ms/272 = 0.8 ms (0.388/2.144)
free_motion_gen: 	9919.3 ms/187 = 53.0 ms (4.2/252.12)
holding_motion_gen: 	4996.9 ms/92 = 54.3 ms (33.565/91.032)
get_stable_4_3: 	0.1 ms/19 = 0.0 ms (0.003/0.014)
get_stable_4_2: 	43.7 ms/54 = 0.8 ms (0.455/2.341)

solve-mean: 1998.9 ms
solve-median: 1241.1 ms
success rate: 88.0 %


## play plan

In [23]:
SIMULATE = False
if (plan is None) or not has_gui():
    disconnect()
else:
    command = postprocess_plan(plan)
    if SIMULATE:
#         wait_for_user('Simulate?')
        command.control()
    else:
#         wait_for_user('Execute?')
        #command.step()
        command.refine(num_steps=10).execute(time_step=0.01)